In [3]:
from DeepLearning.Environments.NoSetupEnv import NoSetupDenseRewardEnv
from DeepLearning.Environments.SetupEnv import SetupRandomWithRoadsEnv
from DeepLearning.Environments.CatanEnv import CatanEnv
from DeepLearning.Environments.SelfPlayEnv import SelfPlayEnv, SelfPlaySetupDotTotalEnv
from DeepLearning.PPO import MaskablePPO
from DeepLearning.GetActionMask import getSetupWithRoadsActionMask, getActionMask
from DeepLearning.GetObservation import getSetupRandomWithRoadsObservation, getObservation
from Agents.AgentModel import AgentMultiModel
import os

os.environ["UPDATE_MODELS"] = "False"
os.environ["MODEL_NAME"] = "None"

# setupOpponentModel = MaskablePPO.load('DeepLearning/Models/SetupOnly_DotTotal_100k.zip')
# opponentModel = MaskablePPO.load('DeepLearning/Models/SelfPlay_SetupDotTotal_7vp_2M.zip')
# opponents = [
#     AgentMultiModel("P1", 1, setupModel=setupOpponentModel, model=opponentModel, fullSetup=False),
#     AgentMultiModel("P1", 1, setupModel=setupOpponentModel, model=opponentModel, fullSetup=False),
#     AgentMultiModel("P2", 2, setupModel=setupOpponentModel, model=opponentModel, fullSetup=False),
#     AgentMultiModel("P3", 3, setupModel=setupOpponentModel, model=opponentModel, fullSetup=False)
# ]

#env = NoSetupDenseRewardEnv(setupModel=MaskablePPO.load('DeepLearning/Models/SetupRandom_wins_1M.zip'))
env = SelfPlayEnv()

info = {
    "env": "SelfPlayEnv",
    "Timesteps": "13M",
    "Opponents": "3x(same model self play)"
}

name = "SelfPlay_7vp_13M"

model = MaskablePPO("MlpPolicy", env, gamma=0.4, verbose=1, getActionMask=getActionMask, getObservation=getObservation, info=info, tensorboard_log="./tensorboard_logs/")
model.learn(total_timesteps=13_000_000, tb_log_name=name)
model.save(f"DeepLearning/Models/{name}")


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Logging to ./tensorboard_logs/SelfPlay_7vp_13M_2


/Users/danieldrummond/Catan/PyCatron/TC2/Client/env/lib/python3.11/site-packages/gymnasium/core.py:311: UserWarning: WARN: env.action_masks to get variables from other wrappers is deprecated and will be removed in v1.0, to get this variable you can do `env.unwrapped.action_masks` for environment variables or `env.get_wrapper_attr('action_masks')` that will search the reminding wrappers.
  logger.warn(


---------------------------------
| rollout/           |          |
|    ep_len_mean     | 198      |
|    ep_rew_mean     | 4.8      |
| time/              |          |
|    fps             | 1067     |
|    iterations      | 1        |
|    time_elapsed    | 1        |
|    total_timesteps | 2048     |
---------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 230         |
|    ep_rew_mean          | 5.88        |
| time/                   |             |
|    fps                  | 839         |
|    iterations           | 2           |
|    time_elapsed         | 4           |
|    total_timesteps      | 4096        |
| train/                  |             |
|    approx_kl            | 0.008137091 |
|    clip_fraction        | 0.12        |
|    clip_range           | 0.2         |
|    entropy_loss         | -0.623      |
|    explained_variance   | -1.34       |
|    learning_rate        | 0.

In [40]:
# Test Trained model using env format, use to debug running environments 

from sb3_contrib.common.maskable.utils import get_action_masks
from DeepLearning.Environments.NoSetupEnv import NoSetupDenseRewardEnv, NoSetupEnv
from DeepLearning.Environments.SetupEnv import SetupRandomWithRoadsEnv
from DeepLearning.Environments.CatanEnv import CatanEnv
from DeepLearning.Environments.SelfPlayEnv import SelfPlayEnv, SelfPlaySetupDotTotalEnv
import os
from Game.CatanPlayer import PlayerStatsTracker
from DeepLearning.PPO import MaskablePPO
from Agents.AgentRandom2 import AgentRandom2
from Agents.AgentMCTS import AgentMCTS
from tabulate import tabulate
from DeepLearning.Stats import headers
import pandas as pd
import random

def run():
    # env = NoSetupDenseRewardEnv(setupModel=MaskablePPO.load('DeepLearning/Models/SetupRandom_wins_1M.zip'))
    os.environ["UPDATE_MODELS"] = "False"
    os.environ["MODEL_NAME"] = "None"
    env = NoSetupEnv(setupModel=MaskablePPO.load('DeepLearning/Models/SetupOnly_DotTotal_100k.zip'))
    modelName = "model_iteration_751"

    # model.save(f"DeepLearning/Models/{modelName}")
    model = MaskablePPO.load(f'DeepLearning/SelfPlayModels/{modelName}.zip')

    rewardList = []
    winner = [0,0,0,0]

    stats = PlayerStatsTracker()
    randomStats = PlayerStatsTracker()

    players = [ AgentRandom2("P0", 0),
                AgentRandom2("P1", 1),
                AgentRandom2("P2", 2),
                AgentRandom2("P3", 3)]

    for episode in range(100):
        done = False
        state, info = env.reset()#players=players)

        while done != True:
            action_masks = get_action_masks(env)
            action, _states = model.predict(state, action_masks=action_masks)
            state, reward, done, _, info = env.step(action.item())
            rewardList.append(reward)

        winner[env.game.gameState.winner] += 1
        
        env.game.gameState.players[0].generatePlayerStats()
        env.game.gameState.players[3].generatePlayerStats()

        stats += env.game.gameState.players[0].stats
        randomStats += env.game.gameState.players[3].stats

    # Collect stats
    opponentName = "AgentRandom"

    stats.getAverages()
    randomStats.getAverages()

    agentData = stats.getList()
    agentData.insert(0, winner[0]/sum(winner))
    agentData.insert(0, modelName)
    randomData = randomStats.getList()
    randomData.insert(0, winner[3]/sum(winner))
    randomData.insert(0, opponentName)

    table = tabulate([agentData, randomData], headers=headers, tablefmt='simple')
    print(table)

    # Save to CSV
    fileName = f'{modelName}_vs_3{opponentName}.csv'
    # df = pd.DataFrame([agentData, randomData], columns=headers)
    # df.to_csv(f'DeepLearning/Data/{fileName}', index=False)


    print("\n\nWinnings: ", winner)

run()

# Brick, ore, wool, wheat, wood

AgentName              WinRate    numTurns    victoryPoints  finalTradeRates                   numRoadsBuilt    devCardsBought  usedDevCards                     settlementsBuilt    citiesBuilt    devCardVP    largestArmy    longestRoad  resourcesReceived                      totalResourcesReceivedPerTurn    totalResourcesDiscarded    totalResourcesStolen  resourcesFromDevCard             totalResourcesFromDevCard  resourcesFromBankTrade             totalResourcesFromBankTrade  finalResourceProduction            setupResourceProduction           totalSetupResourceProduction  setupTradeRates
-------------------  ---------  ----------  ---------------  ------------------------------  ---------------  ----------------  -----------------------------  ------------------  -------------  -----------  -------------  -------------  -----------------------------------  -------------------------------  -------------------------  ----------------------  -----------------------------  --------------

In [11]:
"""
Running Agent simulations
"""
from Agents.AgentRandom2 import AgentRandom2
from Agents.AgentMCTS import AgentMCTS
from Agents.AgentUCT import AgentUCT
from Agents.AgentModel import AgentMultiModel, AgentModel
from Game.CatanGame import *
from CatanSimulator import CreateGame
from DeepLearning.PPO import MaskablePPO
from DeepLearning.Environments.SetupEnv import SetupRandomEnv, SetupRandomWithRoadsEnv, SetupOnlyEnv
from DeepLearning.Environments.NoSetupEnv import NoSetupDenseRewardEnv
from Game.CatanPlayer import PlayerStatsTracker
from tabulate import tabulate
from DeepLearning.Stats import headers
import dill as pickle
import pandas as pd


winner = [0,0,0,0]
player0Stats = PlayerStatsTracker()
player1Stats = PlayerStatsTracker()

# AgentMultiModel("P0", 0, setupModel=MaskablePPO.load("DeepLearning/Models/SetupRoadsSelfPlay_v_SelfPlay_SetupDotTotal_wins_100k.zip"), fullSetup=True, model=MaskablePPO.load("DeepLearning/Models/SelfPlay_SetupDotTotal_7vp_2M.zip")
# AgentMultiModel("P1", 1, setupModel=MaskablePPO.load("DeepLearning/Models/SetupOnly_DotTotal_100k.zip"), fullSetup=False, model=MaskablePPO.load("DeepLearning/Models/SelfPlay_SetupDotTotal_7vp_2M.zip"))

players = [ AgentMultiModel("P0", 0, setupModel=MaskablePPO.load("DeepLearning/Models/SelfPlay_7vp_13M.zip"), fullSetup=True, model=MaskablePPO.load("DeepLearning/Models/SelfPlay_SetupDotTotal_7vp_2M.zip")),
            AgentRandom2("P1", 1),
            AgentRandom2("P2", 2),
            AgentRandom2("P3", 3)]
        

for episode in range(100):
    game = CreateGame(players)
    game = pickle.loads(pickle.dumps(game, -1))
    while True:
        currPlayer = game.gameState.players[game.gameState.currPlayer]

        agentAction = currPlayer.DoMove(game)
        agentAction.ApplyAction(game.gameState)

        if game.gameState.currState == "OVER":
            break
    winner[game.gameState.winner] += 1

    # Stats
    game.gameState.players[0].generatePlayerStats()
    game.gameState.players[1].generatePlayerStats()

    player0Stats += game.gameState.players[0].stats
    player1Stats += game.gameState.players[1].stats

# Collect stats
player0Stats.getAverages()
player1Stats.getAverages()

player0Data = player0Stats.getList()
player1Data = player1Stats.getList()

player0Data.insert(0, winner[0]/sum(winner))
player1Data.insert(0, winner[1]/sum(winner))
player0Data.insert(0, "Player0")
player1Data.insert(0, "Player1")

table = tabulate([player0Data, player1Data], headers=headers, tablefmt='simple')
print(table)


print("\n\nWinnings: ", winner)

# Save to csv
# fileName = f'SelfPlay_SetupDotTotal_7vp_2M__vs__1SetupRandomWins-1M-DenseRewardEnv-10M.csv'
# df = pd.DataFrame([player0Data, player1Data], columns=headers)
# df.to_csv(f'DeepLearning/Data/{fileName}', index=False)

# Brick, ore, wool, wheat, wood

AgentName      WinRate    numTurns    victoryPoints  finalTradeRates                   numRoadsBuilt    devCardsBought  usedDevCards                     settlementsBuilt    citiesBuilt    devCardVP    largestArmy    longestRoad  resourcesReceived                      totalResourcesReceivedPerTurn    totalResourcesDiscarded    totalResourcesStolen  resourcesFromDevCard           totalResourcesFromDevCard  resourcesFromBankTrade           totalResourcesFromBankTrade  finalResourceProduction       setupResourceProduction           totalSetupResourceProduction  setupTradeRates
-----------  ---------  ----------  ---------------  ------------------------------  ---------------  ----------------  -----------------------------  ------------------  -------------  -----------  -------------  -------------  -----------------------------------  -------------------------------  -------------------------  ----------------------  ---------------------------  ---------------------------  ------------

In [14]:
# Load previous models, set the action mask + observation funcitons, save them again
from DeepLearning.PPO import MaskablePPO
from DeepLearning.GetActionMask import getActionMask, getSetupActionMask, getSetupWithRoadsActionMask
from DeepLearning.GetObservation import getObservation, getSetupObservation, getSetupRandomObservation, getObservationNoPhase, getSetupRandomWithRoadsObservation

name = ""

model = MaskablePPO.load(f'DeepLearning/Models/{name}.zip')
print(model.getActionMask)
print(model.getObservation)


# model.getActionMask = getActionMask
# model.getObservation = getObservation

# model.save(f'DeepLearning/Models/{name}.zip')

[0, 0, 0, 0]
